In [ ]:
import os
import json
import requests
import chromadb

from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain.schema import Document
from transformers import pipeline
from langchain_huggingface import HuggingFaceEmbeddings
from langchain_chroma import Chroma
from langchain.chains import RetrievalQA
from langchain import HuggingFacePipeline

from utils.text_data_preprocessing import *


In [2]:
#dump text_data as json if not already done
if not os.path.exists("./text_data.json"):
	directory = "./farmai_training_data"
	text_data =  extract_text(directory)
	with open('text_data.json', 'w') as fp:
	    json.dump(text_data, fp)
else:
	with open('text_data.json') as f:
	    text_data = json.load(f)
	    print(text_data)


{'Pineapple-Growing-Guide.pdf': '200 \n \n4.11.0  PINEAPPLES \n \n4.11.1 Introduction \nineapple production has consistently increased over the years. The main production districts for \npineapple cultivation include; Central region: Kayunga, Luweero, Wakiso (Busi Island), \nMubende; Eastern region: Serere; Western region: Kasese. \nA herbaceous, perennial and heliophile plant, and a member of the Bromeliaceae family, the pineapple \nhas significant nutritional, commercial and industrial potential. Mainly grown for its fruit, the pineapple \ncan be consumed fresh, dried or processed into preserves, drinks or vinegar. The pineapple is a tropical \nP 201 \n \nand subtropical fruit grown in many African countries. Locally the fruit is known as “ Enanansi”. The \nfruit is trade -able and generates a lot of income for farmers who grow it. In Uganda, pineapples are \nmainly grown south of Lake Kyoga and in western Uganda in Ntungamo, Rwampala. central region in \nthe districts of Mukono, Kay

In [3]:

def dict_to_documents(file_dict):
    """
    Convert a dictionary of {filename: content} to LangChain Document objects

    Args:
        file_dict (dict): Dictionary with filename as key, text content as value

    Returns:
        list: List of Document objects
    """
    documents = []

    for filename, content in file_dict.items():
        doc = Document(
            page_content=content,
            metadata={
                "source": filename,
                "filename": os.path.basename(filename),  # Just the filename without path
                "file_extension": os.path.splitext(filename)[1],
                "char_count": len(content),
                "word_count": len(content.split())
            }
        )
        documents.append(doc)

    return documents


In [ ]:
# text to chunks
data = dict_to_documents(text_data)
text_splitter = RecursiveCharacterTextSplitter(
chunk_size=250,
chunk_overlap=20,
separators=["\n\n", "\n", ". ", " ", ""],
keep_separator=True)
all_splits = text_splitter.split_documents(data)


In [6]:

#TODO: switch to model that performs better on manuals. MiniLM is for rapid prototyping
embeddings = HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")


In [ ]:
import chromadb


chroma_client = chromadb.PersistentClient(path="./embeddings")

# Add to Vector database ChromaDB
vectorstore = Chroma.from_documents(
    documents=all_splits,
    collection_name="farmai-embeddings",
    embedding=embeddings,
	persist_directory="./embeddings" #needed to use persistent client
)


In [ ]:
# check vector db response.
# this will become a context to LLM. LLM has to respond from this context
question = 'Which crops to plant after harvesting maize?'
docs = vectorstore.similarity_search(question)


In [ ]:
import re
len(docs)
print(docs[1])


page_content='for ecological reasons, as they increase crop productivity, conserve the soil and increa se soil fertility. Many 
traditional crops, such as pumpkin, sweet potato and beans, are interplanted with maize or other cereal crops' metadata={'source': 'IMPROVING NUTRITION THROUGH HOME GARDENING.pdf', 'filename': 'IMPROVING NUTRITION THROUGH HOME GARDENING.pdf', 'file_extension': '.pdf', 'word_count': 72254, 'char_count': 478716}


In [ ]:
#take user input (cli)
user_question = input("Ask a question")
retrieved_docs = vectorstore.similarity_search(question, k=2)


In [ ]:

print(f"Found {len(retrieved_docs)} relevant documents")

# STEP 2: Extract and combine context
print("\nStep 2: Extracting context...")
context_texts = "".join(doc.page_content for doc in retrieved_docs)
combined_context = "\n\n".join(context_texts)


Found 2 relevant documents

Step 2: Extracting context...


In [ ]:
print("\nStep 3: Creating prompt...")
prompt = f"""Context Information:
{combined_context}

User Question: {user_question}

Instructions: You are providing climate-smart farming advice to women smallholder farmers in Uganda.
Based ONLY on the context provided above, create a very concise 1-2 sentence answer that is:

- SIMPLE & ACTIONABLE: Give specific steps using "You can..." format
- LOCALLY RELEVANT: Reference materials available in Uganda (banana leaves, cassava peels, local wood, etc.)
- TRUSTWORTHY: Reference sources if mentioned in context
- INCLUSIVE: Focus on low-cost practices accessible to smallholders
- CLIMATE-FOCUSED: Address weather challenges

If the context doesn't contain relevant farming advice, respond: "I don't have enough information to provide safe farming advice for that question."
Think step by step.
Answer:"""



Step 3: Creating prompt...


In [29]:

def call_ollama(prompt, model):
    """Send prompt to Ollama API"""
    try:
        response = requests.post(
            'http://localhost:11434/api/generate',
            json={
                'model': model,  # or whatever model you installed
                'prompt': prompt,
                'stream': False
            }
        )
        return response.json()['response']
    except Exception as e:
        return f"LLM Error: {str(e)}"


In [ ]:
# STEP 4: Send to LLM (Example with Ollama)
print("\nStep 4: Getting response...")
model = 'tinyllama'
llm_response = call_ollama(prompt, model)

print(f"\nFinal Answer: {llm_response}")



Step 4: Getting LLM response...

Final Answer: Yes, based on the given material, here are some low-cost climate-smart farming practices suitable for women smallholder farmers in Uganda after harvesting maize:

1. Planting banana leaves: Banana leaves provide excellent shade during hot weather and are essential for improving soil moisture retention. They can be stacked vertically or hung from poles, making them a great option for dry season planting.

2. Using cassava peels: Cassava peels (saplings) are lightweight, rot-resistant, and drought-tolerant, making them an excellent alternative to soil for container crops such as maize or beans. They can also be used as a mulch to protect the soil from heavy rain.

3. Incorporating local wood: Local woods (such as cashew or eucalyptus) are abundant in Uganda and can serve as a valuable addition to farming practices. They have high carbon content and can help regulate carbon dioxide levels in the soil, making them beneficial for soil improvem

zero-shot RAG prompt

Context Information:
{retrieved_context}

User Question: {user_query}

Instructions: You are providing climate-smart farming advice to women smallholder farmers in Uganda. Based ONLY on the context provided above, create a concise 1-2 sentence answer that is:

- SIMPLE & ACTIONABLE: Give specific steps using "You can..." format with clear actions
- LOCALLY RELEVANT: Reference materials commonly available in Uganda (banana leaves, cassava peels, local wood, clay, ash, etc.)
- TRUSTWORTHY: If the context mentions sources like extension services, cooperatives, or farmer experiences, reference them
- INCLUSIVE: Focus on low-cost or free practices accessible to smallholders
- CLIMATE-FOCUSED: Address weather challenges like irregular rains, drought, or flooding

If the context doesn't contain relevant farming advice for the specific question, respond: "I don't have enough information to advise on that your question."

Answer: